In [1]:
import pandas as pd
import plotly.graph_objects as go

# Load data from the Excel file
file_path = 'data1.xlsx'  # Replace with actual path to the .xlsx file
df = pd.read_excel(file_path)

# Convert timestamp column to datetime format
df['timestamp'] = pd.to_datetime(df['time_stamp'], format='%d/%m/%Y %H:%M:%S')  # Adjust the column name if necessary

# Filter out rows where trip is 0 (vehicle off periods)
df_active = df[df['trip'] > 0]

# Aggregate data by trip
trip_stats = df_active.groupby('trip').agg(
    start_time=('timestamp', 'min'),
    end_time=('timestamp', 'max'),
    avg_speed=('vehicle_speed', 'mean'),
    top_speed=('vehicle_speed', 'max'),
    initial_speed=('vehicle_speed', 'first')  # First recorded speed for each trip
).reset_index()

# Calculate additional metrics
trip_stats['trip_duration'] = (trip_stats['end_time'] - trip_stats['start_time']).dt.total_seconds() / 3600  # Trip duration in hours
trip_stats['distance_covered'] = trip_stats['avg_speed'] * trip_stats['trip_duration']  # Distance = speed * time

# Create a figure for plotting
fig = go.Figure()

# Add line trace for vehicle speed over time
fig.add_trace(go.Scatter(
    x=df['timestamp'],
    y=df['vehicle_speed'],
    mode='lines',
    name='Vehicle Speed',
    line=dict(color='blue', width=1),
    hoverinfo='x+y'
))

# Highlight points where engine_rpm > 4000
high_rpm = df[df['engine_rpm'] > 4000]

fig.add_trace(go.Scatter(
    x=high_rpm['timestamp'],
    y=high_rpm['vehicle_speed'],
    mode='markers',
    name='RPM > 4000',
    marker=dict(color='red', size=8, symbol='circle'),
    hoverinfo='x+y'
))

# Add lines for average speed, top speed, distance covered, and average acceleration for each trip
for _, row in trip_stats.iterrows():
    # Average speed trace
    fig.add_trace(go.Scatter(
        x=[row['start_time'], row['end_time']],
        y=[row['avg_speed'], row['avg_speed']],
        mode='lines',
        name=f'Avg Speed Trip {row["trip"]}',
        line=dict(color='red', width=2, dash='dash')
    ))

    # Top speed trace
    fig.add_trace(go.Scatter(
        x=[row['start_time'], row['end_time']],
        y=[row['top_speed'], row['top_speed']],
        mode='lines',
        name=f'Top Speed Trip {row["trip"]}',
        line=dict(color='green', width=2, dash='dot')
    ))

    # Annotate distance covered for the trip
    fig.add_trace(go.Scatter(
        x=[row['end_time']],
        y=[row['top_speed']],
        mode='markers+text',
        text=f'Distance: {row["distance_covered"]:.2f} km',
        textposition='top center',
        showlegend=False
    ))



# Update layout with interactive features
fig.update_layout(
    title='Vehicle Speed Over Time with Trip Statistics',
    xaxis=dict(
        title='Time',
        type='date',
        rangeslider=dict(visible=True),  # Enable range slider for zoom control
        showspikes=True,
        spikemode='across',  # Spike line when hovering
        spikedash='dash',
    ),
    yaxis=dict(
        title='Speed (km/h)',
        range=[0, df['vehicle_speed'].max() + 10],  # Adjust the y-axis range
        showspikes=True,  # Spike on hover
    ),
    hovermode="x unified",  # Show single hover label across traces
    template="plotly_white"  # Clean and clear look
)

# Display the figure
fig.show()


In [2]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

def load_and_prepare_data(file_path):
    # Load data
    df = pd.read_excel(file_path)

    # Convert timestamp to datetime
    df['timestamp'] = pd.to_datetime(df['time_stamp'], format='%d/%m/%Y %H:%M:%S')

    # Filter out inactive trips
    df_active = df[df['trip'] > 0]
    return df, df_active

def calculate_acceleration(df_active):
    # Calculate time differences in seconds
    df_active['time_diff'] = df_active['timestamp'].diff().dt.total_seconds()

    # Calculate speed differences (assuming speed is in km/h)
    df_active['speed_diff'] = df_active['vehicle_speed'].diff()

    # Calculate acceleration in km/h² (change in speed divided by time in hours)
    df_active['acceleration'] = df_active['speed_diff'] / df_active['time_diff']

    # Drop any NaN values (first row will have NaN due to diff)
    df_active = df_active.dropna(subset=['acceleration'])

    return df_active

def calculate_rms_acceleration(df_active):
    # Calculate RMS acceleration for each trip
    trip_rms_accel = df_active.groupby('trip').apply(lambda x: np.sqrt(np.mean(x['acceleration']**2)))
    return trip_rms_accel

def aggregate_trip_stats(df_active, trip_rms_accel):
    # Aggregate data by trip
    trip_stats = df_active.groupby('trip').agg(
        start_time=('timestamp', 'min'),
        end_time=('timestamp', 'max'),
        avg_speed=('vehicle_speed', 'mean'),
        top_speed=('vehicle_speed', 'max'),
        initial_speed=('vehicle_speed', 'first'),
        avg_acceleration=('acceleration', 'mean')
    ).reset_index()

    # Add RMS acceleration to trip stats
    trip_stats['rms_acceleration'] = trip_rms_accel.values

    return trip_stats

def classify_aggressive_trips(trip_stats, rms_threshold=2.0):
    # Classify trips as aggressive or non-aggressive based on RMS acceleration
    trip_stats['is_aggressive'] = trip_stats['rms_acceleration'] > rms_threshold

    # Print classification result
    print(trip_stats[['trip', 'rms_acceleration', 'is_aggressive']])

    return trip_stats

def plot_data(df, trip_stats):
    fig = go.Figure()

    # Vehicle speed over time
    fig.add_trace(go.Scatter(
        x=df['timestamp'],
        y=df['vehicle_speed'],
        mode='lines',
        name='Vehicle Speed',
        line=dict(color='blue', width=1),
        hoverinfo='x+y'
    ))

    # Plot acceleration over time
    fig.add_trace(go.Scatter(
        x=df['timestamp'],
        y=df['acceleration'],
        mode='lines',
        name='Acceleration',
        line=dict(color='orange', width=1),
        hoverinfo='x+y'
    ))

    # Add traces for each trip's average acceleration and classify aggressive trips
    for _, row in trip_stats.iterrows():
        color = 'red' if row['is_aggressive'] else 'green'
        fig.add_trace(go.Scatter(
            x=[row['start_time'], row['end_time']],
            y=[row['avg_acceleration'], row['avg_acceleration']],
            mode='lines+markers',
            name=f'Avg Acc Trip {row["trip"]} ({ "Aggressive" if row["is_aggressive"] else "Non-aggressive" })',
            line=dict(color=color, width=2, dash='dash'),
            marker=dict(symbol='circle', size=6),
            hoverinfo='x+y+text',
            text=f'RMS Acceleration: {row["rms_acceleration"]:.2f} km/h/s'
        ))

    # Update layout
    fig.update_layout(
        title='Vehicle Speed and Acceleration Over Time (Aggressive vs Non-Aggressive)',
        xaxis=dict(
            title='Time',
            type='date',
            rangeslider=dict(visible=True),
            showspikes=True,
            spikemode='across',
            spikedash='dash'
        ),
        yaxis=dict(
            title='Speed (km/h) / Acceleration (km/h/s)',
            showspikes=True
        ),
        hovermode="x unified",
        template="plotly_white"
    )

    fig.show()

# File path
file_path = 'data1.xlsx'  # Replace with the actual path

# Execute functions
df, df_active = load_and_prepare_data(file_path)
df_active = calculate_acceleration(df_active)
trip_rms_accel = calculate_rms_acceleration(df_active)
trip_stats = aggregate_trip_stats(df_active, trip_rms_accel)
trip_stats = classify_aggressive_trips(trip_stats, rms_threshold=2.0)
plot_data(df_active, trip_stats)


C:\Users\umer\AppData\Local\Temp\ipykernel_7704\2151331496.py:18: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\umer\AppData\Local\Temp\ipykernel_7704\2151331496.py:21: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\umer\AppData\Local\Temp\ipykernel_7704\2151331496.py:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d

    trip  rms_acceleration  is_aggressive
0      1          2.161206           True
1      2          2.041039           True
2      3          1.704241          False
3      4          2.250450           True
4      5          4.217095           True
..   ...               ...            ...
65    66          0.992157          False
66    67          1.925593          False
67    68          2.255262           True
68    69          2.236650           True
69    70          1.484010          False

[70 rows x 3 columns]


In [3]:
import pandas as pd
import plotly.graph_objects as go

def load_and_prepare_data(file_path):
    # Load data
    df = pd.read_excel(file_path)

    # Convert timestamp to datetime
    df['timestamp'] = pd.to_datetime(df['time_stamp'], format='%d/%m/%Y %H:%M:%S')

    # Filter out inactive trips
    df_active = df[df['trip'] > 0]
    return df, df_active

def calculate_acceleration(df_active):
    # Calculate time differences in seconds
    df_active['time_diff'] = df_active['timestamp'].diff().dt.total_seconds()

    # Calculate speed differences (assuming speed is in km/h)
    df_active['speed_diff'] = df_active['vehicle_speed'].diff()

    # Calculate acceleration in km/h² (change in speed divided by time in hours)
    df_active['acceleration'] = df_active['speed_diff'] / (df_active['time_diff'] / 3600)


    # Drop any NaN values (first row will have NaN due to diff)
    df_active = df_active.dropna(subset=['acceleration'])

    return df_active

def aggregate_trip_stats(df_active):
    # Aggregate data by trip
    trip_stats = df_active.groupby('trip').agg(
        start_time=('timestamp', 'min'),
        end_time=('timestamp', 'max'),
        avg_acceleration=('acceleration', 'mean')
    ).reset_index()

    return trip_stats

def plot_acceleration(df, trip_stats):
    fig = go.Figure()

    # Plot acceleration over time
    fig.add_trace(go.Scatter(
        x=df['timestamp'],
        y=df['acceleration'],
        mode='lines',
        name='Acceleration',
        line=dict(color='orange', width=1),
        hoverinfo='x+y'
    ))

    # Add traces for each trip's average acceleration
    for _, row in trip_stats.iterrows():
        fig.add_trace(go.Scatter(
            x=[row['start_time'], row['end_time']],
            y=[row['avg_acceleration'], row['avg_acceleration']],
            mode='lines',
            name=f'Avg Acceleration Trip {row["trip"]}',
            line=dict(color='red', width=2, dash='dash')
        ))

    # Update layout
    fig.update_layout(
        title='Acceleration Over Time',
        xaxis=dict(
            title='Time',
            type='date',
            rangeslider=dict(visible=True),
            showspikes=True,
            spikemode='across',
            spikedash='dash'
        ),
        yaxis=dict(
            title='Acceleration (km/h²)',
            showspikes=True
        ),
        hovermode="x unified",
        template="plotly_white"
    )

    fig.show()

# File path
file_path = 'data1.xlsx'  # Replace with the actual path

# Execute functions
df, df_active = load_and_prepare_data(file_path)
df_active = calculate_acceleration(df_active)
trip_stats = aggregate_trip_stats(df_active)
plot_acceleration(df_active, trip_stats)


C:\Users\umer\AppData\Local\Temp\ipykernel_7704\3373720147.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\umer\AppData\Local\Temp\ipykernel_7704\3373720147.py:20: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\umer\AppData\Local\Temp\ipykernel_7704\3373720147.py:23: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d

In [9]:
import pandas as pd
import plotly.graph_objects as go

# Load data from the Excel file
file_path = 'data1.xlsx'  # Replace with actual path to the .xlsx file
df = pd.read_excel(file_path)

# Convert timestamp column to datetime format
df['timestamp'] = pd.to_datetime(df['time_stamp'], format='%d/%m/%Y %H:%M:%S')  # Adjust the column name if necessary

# Filter out rows where trip is 0 (vehicle off periods)
df_active = df[df['trip'] > 0]

# Calculate fuel consumption rate using mass air flow rate
# This is a more realistic estimation
# Assume that 1 kg of air requires about 0.2 liters of fuel
# and air flow rate is in kg/h
df_active['fuel_consumption_l_per_h'] = df_active['mass_air_flow_rate'] * 0.2

# Avoid division by zero for speed = 0
df_active['vehicle_speed'] = df_active['vehicle_speed'].replace(0, 1e-5)

# Calculate fuel consumption in kilometers per liter (km/L)
df_active['fuel_consumption_km_per_l'] = df_active['vehicle_speed'] / df_active['fuel_consumption_l_per_h']

# Replace infinite values (result of division by zero) with NaN
df_active['fuel_consumption_km_per_l'].replace([float('inf'), -float('inf')], float('nan'), inplace=True)

# Aggregate data by trip
trip_stats = df_active.groupby('trip').agg(
    start_time=('timestamp', 'min'),
    end_time=('timestamp', 'max'),
    avg_speed=('vehicle_speed', 'mean'),
    top_speed=('vehicle_speed', 'max'),
    initial_speed=('vehicle_speed', 'first'),  # First recorded speed for each trip
    avg_fuel_consumption=('fuel_consumption_km_per_l', 'mean')  # Average fuel consumption per trip
).reset_index()

# Calculate additional metrics
trip_stats['trip_duration'] = (trip_stats['end_time'] - trip_stats['start_time']).dt.total_seconds() / 3600  # Trip duration in hours
trip_stats['distance_covered'] = trip_stats['avg_speed'] * trip_stats['trip_duration']  # Distance = speed * time

# Create a figure for plotting
fig = go.Figure()

# Add line trace for vehicle speed over time
fig.add_trace(go.Scatter(
    x=df_active['timestamp'],
    y=df_active['vehicle_speed'],
    mode='lines',
    name='Vehicle Speed',
    line=dict(color='blue', width=1),
    hoverinfo='x+y'
))

# Add line trace for fuel consumption over time
fig.add_trace(go.Scatter(
    x=df_active['timestamp'],
    y=df_active['fuel_consumption_km_per_l'],
    mode='lines',
    name='Fuel Consumption (km/L)',
    line=dict(color='orange', width=1),
    hoverinfo='x+y'
))

# Highlight points where engine_rpm > 4000
high_rpm = df_active[df_active['engine_rpm'] > 4000]
fig.add_trace(go.Scatter(
    x=high_rpm['timestamp'],
    y=high_rpm['vehicle_speed'],
    mode='markers',
    name='RPM > 4000',
    marker=dict(color='red', size=8, symbol='circle'),
    hoverinfo='x+y'
))

# Add lines for average speed, top speed, distance covered, and average fuel consumption for each trip
for _, row in trip_stats.iterrows():
    # Average speed trace
    fig.add_trace(go.Scatter(
        x=[row['start_time'], row['end_time']],
        y=[row['avg_speed'], row['avg_speed']],
        mode='lines',
        name=f'Avg Speed Trip {row["trip"]}',
        line=dict(color='red', width=2, dash='dash')
    ))

    # Top speed trace
    fig.add_trace(go.Scatter(
        x=[row['start_time'], row['end_time']],
        y=[row['top_speed'], row['top_speed']],
        mode='lines',
        name=f'Top Speed Trip {row["trip"]}',
        line=dict(color='green', width=2, dash='dot')
    ))

    # Annotate distance covered for the trip
    fig.add_trace(go.Scatter(
        x=[row['end_time']],
        y=[row['top_speed']],
        mode='markers+text',
        text=f'Distance: {row["distance_covered"]:.2f} km',
        textposition='top center',
        showlegend=False
    ))

    # Annotate average fuel consumption for the trip
    fig.add_trace(go.Scatter(
        x=[row['end_time']],
        y=[row['avg_speed']],
        mode='markers+text',
        text=f'Avg Fuel: {row["avg_fuel_consumption"]:.2f} km/L',
        textposition='bottom center',
        showlegend=False
    ))

# Update layout with interactive features
fig.update_layout(
    title='Vehicle Speed and Fuel Consumption Over Time with Trip Statistics',
    xaxis=dict(
        title='Time',
        type='date',
        rangeslider=dict(visible=True),  # Enable range slider for zoom control
        showspikes=True,
        spikemode='across',  # Spike line when hovering
        spikedash='dash',
    ),
    yaxis=dict(
        title='Speed (km/h) / Fuel Consumption (km/L)',
        range=[0, max(df_active['vehicle_speed'].max(), df_active['fuel_consumption_km_per_l'].max()) + 10],  # Adjust the y-axis range
        showspikes=True,  # Spike on hover
    ),
    hovermode="x unified",  # Show single hover label across traces
    template="plotly_white"  # Clean and clear look
)

# Display the figure
fig.show()


C:\Users\umer\AppData\Local\Temp\ipykernel_7704\559106381.py:18: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\umer\AppData\Local\Temp\ipykernel_7704\559106381.py:21: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\umer\AppData\Local\Temp\ipykernel_7704\559106381.py:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

In [7]:
import pandas as pd
import plotly.graph_objects as go

# Load data from the Excel file
file_path = 'data1.xlsx'  # Replace with actual path to the .xlsx file
df = pd.read_excel(file_path)

# Convert timestamp column to datetime format
df['timestamp'] = pd.to_datetime(df['time_stamp'], format='%d/%m/%Y %H:%M:%S')  # Adjust the column name if necessary

# Filter out rows where trip is 0 (vehicle off periods)
df_active = df[df['trip'] > 0]

# Adjusted parameters for fuel consumption estimation (empirical values)
fuel_consumption_rate_per_rpm = 0.0005  # Example: liters per RPM, adjust this
fuel_consumption_rate_per_load = 0.02  # Example: liters per engine load unit, adjust this

# Calculate fuel consumption rate (L/h) using RPM and engine load
df_active['fuel_consumption_l_per_h'] = (df_active['engine_rpm'] * fuel_consumption_rate_per_rpm) + (df_active['calculated_engine_load'] * fuel_consumption_rate_per_load)

# Avoid division by zero for speed = 0
df_active['vehicle_speed'] = df_active['vehicle_speed'].replace(0, 1e-5)

# Calculate fuel consumption in kilometers per liter (km/L)
df_active['fuel_consumption_km_per_l'] = df_active['vehicle_speed'] / df_active['fuel_consumption_l_per_h']

# Replace infinite values (result of division by zero) with NaN
df_active['fuel_consumption_km_per_l'].replace([float('inf'), -float('inf')], float('nan'), inplace=True)

# Aggregate data by trip
trip_stats = df_active.groupby('trip').agg(
    start_time=('timestamp', 'min'),
    end_time=('timestamp', 'max'),
    avg_speed=('vehicle_speed', 'mean'),
    top_speed=('vehicle_speed', 'max'),
    initial_speed=('vehicle_speed', 'first'),  # First recorded speed for each trip
    avg_fuel_consumption=('fuel_consumption_km_per_l', 'mean')  # Average fuel consumption per trip
).reset_index()

# Calculate additional metrics
trip_stats['trip_duration'] = (trip_stats['end_time'] - trip_stats['start_time']).dt.total_seconds() / 3600  # Trip duration in hours
trip_stats['distance_covered'] = trip_stats['avg_speed'] * trip_stats['trip_duration']  # Distance = speed * time

# Create a figure for plotting
fig = go.Figure()

# Add line trace for vehicle speed over time
fig.add_trace(go.Scatter(
    x=df_active['timestamp'],
    y=df_active['vehicle_speed'],
    mode='lines',
    name='Vehicle Speed',
    line=dict(color='blue', width=1),
    hoverinfo='x+y'
))

# Highlight points where engine_rpm > 4000
high_rpm = df_active[df_active['engine_rpm'] > 4000]
fig.add_trace(go.Scatter(
    x=high_rpm['timestamp'],
    y=high_rpm['vehicle_speed'],
    mode='markers',
    name='RPM > 4000',
    marker=dict(color='red', size=8, symbol='circle'),
    hoverinfo='x+y'
))

# Add lines for average speed, top speed, distance covered, and average fuel consumption for each trip
for _, row in trip_stats.iterrows():
    # Average speed trace
    fig.add_trace(go.Scatter(
        x=[row['start_time'], row['end_time']],
        y=[row['avg_speed'], row['avg_speed']],
        mode='lines',
        name=f'Avg Speed Trip {row["trip"]}',
        line=dict(color='red', width=2, dash='dash')
    ))

    # Top speed trace
    fig.add_trace(go.Scatter(
        x=[row['start_time'], row['end_time']],
        y=[row['top_speed'], row['top_speed']],
        mode='lines',
        name=f'Top Speed Trip {row["trip"]}',
        line=dict(color='green', width=2, dash='dot')
    ))

    # Annotate distance covered for the trip
    fig.add_trace(go.Scatter(
        x=[row['end_time']],
        y=[row['top_speed']],
        mode='markers+text',
        text=f'Distance: {row["distance_covered"]:.2f} km',
        textposition='top center',
        showlegend=False
    ))

    # Annotate average fuel consumption for the trip (without plotting fuel consumption line)
    fig.add_trace(go.Scatter(
        x=[row['end_time']],
        y=[row['avg_speed']],
        mode='markers+text',
        text=f'Avg Fuel: {row["avg_fuel_consumption"]:.2f} km/L',
        textposition='bottom center',
        showlegend=False
    ))


# Update layout with interactive features
fig.update_layout(
    title='Vehicle Speed Over Time with Trip Statistics',
    xaxis=dict(
        title='Time',
        type='date',
        rangeslider=dict(visible=True),  # Enable range slider for zoom control
        showspikes=True,
        spikemode='across',  # Spike line when hovering
        spikedash='dash',
    ),
    yaxis=dict(
        title='Speed (km/h)',
        range=[0, df_active['vehicle_speed'].max() + 10],  # Adjust the y-axis range
        showspikes=True,  # Spike on hover
    ),
    hovermode="x unified",  # Show single hover label across traces
    template="plotly_white"  # Clean and clear look
)


# Display the figure
fig.show()


C:\Users\umer\AppData\Local\Temp\ipykernel_10056\671313915.py:19: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\umer\AppData\Local\Temp\ipykernel_10056\671313915.py:22: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\umer\AppData\Local\Temp\ipykernel_10056\671313915.py:25: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d